# **Tutorial** - Topic Modeling with BERTopic
(last updated 01-09-2022)

In this tutorial we will be exploring how to use BERTopic to create topics from the well-known 20Newsgroups dataset. The most frequent use-cases and methods are discussed together with important parameters to keep a look out for.


## BERTopic
BERTopic is a topic modeling technique that leverages 🤗 transformers and a custom class-based TF-IDF to create dense clusters allowing for easily interpretable topics whilst keeping important words in the topic descriptions.

<br>

<img src="https://raw.githubusercontent.com/MaartenGr/BERTopic/master/images/logo.png" width="40%">

# Enabling the GPU

First, you'll need to enable GPUs for the notebook:

- Navigate to Edit→Notebook Settings
- select GPU from the Hardware Accelerator drop-down

[Reference](https://colab.research.google.com/notebooks/gpu.ipynb)

# **Installing BERTopic**

We start by installing BERTopic from PyPi:

In [2]:
%%capture
!pip install bertopic

## Restart the Notebook
After installing BERTopic, some packages that were already loaded were updated and in order to correctly use them, we should now restart the notebook.

From the Menu:

Runtime → Restart Runtime

# Data
For this example, we use the popular 20 Newsgroups dataset which contains roughly 18000 newsgroups posts

In [3]:
from sklearn.datasets import fetch_20newsgroups
docs = fetch_20newsgroups(subset='all',  remove=('headers', 'footers', 'quotes'))['data']

In [4]:
docs[:2]

["\n\nI am sure some bashers of Pens fans are pretty confused about the lack\nof any kind of posts about the recent Pens massacre of the Devils. Actually,\nI am  bit puzzled too and a bit relieved. However, I am going to put an end\nto non-PIttsburghers' relief with a bit of praise for the Pens. Man, they\nare killing those Devils worse than I thought. Jagr just showed you why\nhe is much better than his regular season stats. He is also a lot\nfo fun to watch in the playoffs. Bowman should let JAgr have a lot of\nfun in the next couple of games since the Pens are going to beat the pulp out of Jersey anyway. I was very disappointed not to see the Islanders lose the final\nregular season game.          PENS RULE!!!\n\n",
 'My brother is in the market for a high-performance video card that supports\nVESA local bus with 1-2MB RAM.  Does anyone have suggestions/ideas on:\n\n  - Diamond Stealth Pro Local Bus\n\n  - Orchid Farenheit 1280\n\n  - ATI Graphics Ultra Pro\n\n  - Any other high-per

In [5]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [11]:
import pandas as pd
df = pd.read_csv("/content/drive/MyDrive/dataset/data_for_rnn.csv", index_col=0)
df.head()
docs_2 = df["comment_cleaned"].to_list()
#docs_2

# **Topic Modeling**

In this example, we will go through the main components of BERTopic and the steps necessary to create a strong topic model.




## Training

We start by instantiating BERTopic. We set language to `english` since our documents are in the English language. If you would like to use a multi-lingual model, please use `language="multilingual"` instead.

We will also calculate the topic probabilities. However, this can slow down BERTopic significantly at large amounts of data (>100_000 documents). It is advised to turn this off if you want to speed up the model.


In [46]:
from bertopic.representation import KeyBERTInspired
from bertopic import BERTopic

# Create your representation model
representation_model = KeyBERTInspired()

# Use the representation model in BERTopic on top of the default pipeline
topic_model = BERTopic(representation_model=representation_model)

In [47]:
topic_model = BERTopic(language="multilingual", calculate_probabilities=True, verbose=True)
topics, probs = topic_model.fit_transform(docs_2)

Batches:   0%|          | 0/730 [00:00<?, ?it/s]

2023-11-25 17:39:02,041 - BERTopic - Transformed documents to Embeddings
2023-11-25 17:39:35,554 - BERTopic - Reduced dimensionality
2023-11-25 17:43:24,988 - BERTopic - Clustered reduced embeddings


**NOTE**: Use `language="multilingual"` to select a model that support 50+ languages.

## Extracting Topics
After fitting our model, we can start by looking at the results. Typically, we look at the most frequent topics first as they best represent the collection of documents.

In [48]:
freq = topic_model.get_topic_info(); freq.head(5)

Topic  Count                                   Name  \
0     -1   8148      -1_plus_articles_article_commande   
1      0    436    0_rapidité_livraison_vitesse_remise   
2      1    335   1_parfait_exactement_déroulé_voulais   
3      2    314  2_rapide_livraison_rapides_livraisons   
4      3    302   3_rapidité_rapiditée_exp_ponctualite   

                                      Representation  \
0  [plus, articles, article, commande, redoute, r...   
1  [rapidité, livraison, vitesse, remise, facteur...   
2  [parfait, exactement, déroulé, voulais, parfai...   
3  [rapide, livraison, rapides, livraisons, , , ,...   
4  [rapidité, rapiditée, exp, ponctualite, pareil...   

                                 Representative_Docs  
0  [très satisfaite redoute trouvé article corres...  
1  [rapidité livraison, rapidité livraison, rapid...  
2                        [parfait, parfait, parfait]  
3  [livraison rapide, livraison rapide, livraison...  
4                     [rapidité, rapidité, rapidité]

-1 refers to all outliers and should typically be ignored. Next, let's take a look at a frequent topic that were generated:

In [57]:
topic_model.get_topic(0)  # Select the most frequent topic

[('rapidité', 0.048859883068173196),
 ('livraison', 0.022281272222652793),
 ('vitesse', 0.01506367655419365),
 ('remise', 0.006797445846003525),
 ('facteur', 0.004984272453855562),
 ('grande', 0.0047557311760032155),
 ('sécurisée', 0.004467385456134609),
 ('modes', 0.004338476379172937),
 ('peur', 0.004025003607466181),
 ('étonnée', 0.003938192424758481)]

**NOTE**: BERTopic is stocastich which mmeans that the topics might differ across runs. This is mostly due to the stocastisch nature of UMAP.

In [19]:
### Attributes

## Attributes

There are a number of attributes that you can access after having trained your BERTopic model:


| Attribute | Description |
|------------------------|---------------------------------------------------------------------------------------------|
| topics_               | The topics that are generated for each document after training or updating the topic model. |
| probabilities_ | The probabilities that are generated for each document if HDBSCAN is used. |
| topic_sizes_           | The size of each topic                                                                      |
| topic_mapper_          | A class for tracking topics and their mappings anytime they are merged/reduced.             |
| topic_representations_ | The top *n* terms per topic and their respective c-TF-IDF values.                             |
| c_tf_idf_              | The topic-term matrix as calculated through c-TF-IDF.                                       |
| topic_labels_          | The default labels for each topic.                                                          |
| custom_labels_         | Custom labels for each topic as generated through `.set_topic_labels`.                                                               |
| topic_embeddings_      | The embeddings for each topic if `embedding_model` was used.                                                              |
| representative_docs_   | The representative documents for each topic if HDBSCAN is used.                                                |

For example, to access the predicted topics for the first 10 documents, we simply run the following:

In [60]:
topic_model.topic_labels_

{-1: '-1_plus_articles_article_commande',
 0: '0_rapidité_livraison_vitesse_remise',
 1: '1_parfait_exactement_déroulé_voulais',
 2: '2_rapide_livraison_rapides_livraisons',
 3: '3_rapidité_rapiditée_exp_ponctualite',
 4: '4_délais_délai_respecté_respect',
 5: '5_coton_couette_housse_lavage',
 6: '6_site_internet_clair_utilisation',
 7: '7_cliente_depuis_années_ans',
 8: '8_chaussures_sandales_paire_pieds',
 9: '9_achats_achat_satisfaite_vendeuse',
 10: '10_vêtements_vêtement_robe_habits',
 11: '11_achat_achats_satisfaite_magasin',
 12: '12_rapport_prix_bon_excellent',
 13: '13_couleur_couleurs_jaune_coloris',
 14: '14_tailles_taille_dimensions_jean',
 15: '15_mail_téléphone_message_téléphonique',
 16: '16_respecté_respect_délais_délai',
 17: '17_extrêmement_rapide_très_livraison',
 18: '18_design_is_bonne_beau',
 19: '19_ras_tél_personnes_',
 20: '20_envoi_rapidité_extrême_ultra',
 21: '21_envoi_envoie_aimée_produit',
 22: '22_réception_reception_mail_enregistrer',
 23: '23_linge_mais

# **Visualization**
There are several visualization options available in BERTopic, namely the visualization of topics, probabilities and topics over time. Topic modeling is, to a certain extent, quite subjective. Visualizations help understand the topics that were created.

## Visualize Topics
After having trained our `BERTopic` model, we can iteratively go through perhaps a hundred topic to get a good
understanding of the topics that were extract. However, that takes quite some time and lacks a global representation.
Instead, we can visualize the topics that were generated in a way very similar to
[LDAvis](https://github.com/cpsievert/LDAvis):

In [52]:
topic_model.visualize_topics()

## Visualize Topic Probabilities

The variable `probabilities` that is returned from `transform()` or `fit_transform()` can
be used to understand how confident BERTopic is that certain topics can be found in a document.

To visualize the distributions, we simply call:

In [61]:
topic_model.visualize_distribution(probs[200], min_probability=0.015)

## Visualize Topic Hierarchy

The topics that were created can be hierarchically reduced. In order to understand the potential hierarchical structure of the topics, we can use scipy.cluster.hierarchy to create clusters and visualize how they relate to one another. This might help selecting an appropriate nr_topics when reducing the number of topics that you have created.

In [62]:
topic_model.visualize_hierarchy(top_n_topics=50)

## Visualize Terms

We can visualize the selected terms for a few topics by creating bar charts out of the c-TF-IDF scores for each topic representation. Insights can be gained from the relative c-TF-IDF scores between and within topics. Moreover, you can easily compare topic representations to each other.

In [63]:
topic_model.visualize_barchart(top_n_topics=15)

## Visualize Topic Similarity
Having generated topic embeddings, through both c-TF-IDF and embeddings, we can create a similarity matrix by simply applying cosine similarities through those topic embeddings. The result will be a matrix indicating how similar certain topics are to each other.

In [56]:
topic_model.visualize_heatmap(n_clusters=20, width=1000, height=1000)

## Visualize Term Score Decline
Topics are represented by a number of words starting with the best representative word. Each word is represented by a c-TF-IDF score. The higher the score, the more representative a word to the topic is. Since the topic words are sorted by their c-TF-IDF score, the scores slowly decline with each word that is added. At some point adding words to the topic representation only marginally increases the total c-TF-IDF score and would not be beneficial for its representation.

To visualize this effect, we can plot the c-TF-IDF scores for each topic by the term rank of each word. In other words, the position of the words (term rank), where the words with the highest c-TF-IDF score will have a rank of 1, will be put on the x-axis. Whereas the y-axis will be populated by the c-TF-IDF scores. The result is a visualization that shows you the decline of c-TF-IDF score when adding words to the topic representation. It allows you, using the elbow method, the select the best number of words in a topic.


In [28]:
topic_model.visualize_term_rank()

# **Topic Representation**
After having created the topic model, you might not be satisfied with some of the parameters you have chosen. Fortunately, BERTopic allows you to update the topics after they have been created.

This allows for fine-tuning the model to your specifications and wishes.

## Update Topics
When you have trained a model and viewed the topics and the words that represent them,
you might not be satisfied with the representation. Perhaps you forgot to remove
stopwords or you want to try out a different `n_gram_range`. We can use the function `update_topics` to update
the topic representation with new parameters for `c-TF-IDF`:


In [64]:
topic_model.update_topics(docs_2, n_gram_range=(1, 2))

In [65]:
topic_model.get_topic(0)   # We select topic that we viewed before

[('livraison rapidité', 0.2286670380839954),
 ('rapidité livraison', 0.10425069134108222),
 ('rapidité', 0.046631668535652024),
 ('livraison', 0.02180450549208755),
 ('livraison vitesse', 0.013453737654174285),
 ('vitesse livraison', 0.01154110286443405),
 ('vitesse', 0.009375648305375944),
 ('grande rapidité', 0.00785050280231242),
 ('remise rapidité', 0.00677399005036711),
 ('livraison réactivité', 0.005754652813509524)]

## Topic Reduction
We can also reduce the number of topics after having trained a BERTopic model. The advantage of doing so,
is that you can decide the number of topics after knowing how many are actually created. It is difficult to
predict before training your model how many topics that are in your documents and how many will be extracted.
Instead, we can decide afterwards how many topics seems realistic:





In [66]:
topic_model.reduce_topics(docs_2, nr_topics=15)

2023-11-25 17:52:14,283 - BERTopic - Reduced number of topics from 421 to 15


In [69]:
# Access the newly updated topics with:
topic_model2.topic_labels_

{-1: '-1_commande_livraison_très_plus',
 0: '0_qualité_prix_rapide_produits',
 1: '1_rapidité_rapide_rapide livraison_rapidité livraison',
 2: '2_parfait_parfait parfait_parfait parfait parfait_bien',
 3: '3_délai_délais_délai livraison_livraison',
 4: '4_ras ras_ras ras ras_ras_très',
 5: '5_articles_article_qualité articles_qualité',
 6: '6_réception_colis_téléphone_commande',
 7: '7_site_facile_site très_internet',
 8: '8_service_cliente_depuis_client',
 9: '9_photos_photo_conforme photo_conforme',
 10: '10_vêtements_linge_robe_linge maison',
 11: '11_expédition_rapidité expédition_expédition rapidité_expédition rapidité expédition',
 12: '12_attentes_conforme attentes_attentes livraison_conforme',
 13: '13_rien_rien dire_rien rien_dire',
 14: '14_simplicité_facile_simple_rapidité simplicité',
 15: '15_choix_choix rapidité_choix livraison_choix choix',
 16: '16_couleur_couleurs_coloris_qualité',
 17: '17_retour_remboursement_retours_facilité',
 18: '18_chaussures_paire_sandales_boît

# **Search Topics**
After having trained our model, we can use `find_topics` to search for topics that are similar
to an input search_term. Here, we are going to be searching for topics that closely relate the
search term "vehicle". Then, we extract the most similar topic and check the results:

In [44]:
similar_topics, similarity = topic_model2.find_topics("relais", top_n=5); similar_topics

[-1, 4, 6, 17, 5]

In [45]:
topic_model2.get_topic(1)

[('rapidité', 0.07215634252843357),
 ('rapide', 0.04927878464499001),
 ('rapide livraison', 0.04585959727313023),
 ('rapidité livraison', 0.04559316922098303),
 ('livraison rapidité', 0.04465038050920167),
 ('rapidité livraison rapidité', 0.04325036561424531),
 ('rapidité rapidité', 0.0429685092438545),
 ('rapide livraison rapide', 0.04294716773755117),
 ('livraison', 0.041589456818049306),
 ('envoi', 0.04152699188882891)]

# **Model serialization**
The model and its internal settings can easily be saved. Note that the documents and embeddings will not be saved. However, UMAP and HDBSCAN will be saved.

In [ ]:
# Save model
topic_model.save("my_model")

In [ ]:
# Load model
my_model = BERTopic.load("my_model")

# **Embedding Models**
The parameter `embedding_model` takes in a string pointing to a sentence-transformers model, a SentenceTransformer, or a Flair DocumentEmbedding model.

## Sentence-Transformers
You can select any model from sentence-transformers here and pass it through BERTopic with embedding_model:



In [ ]:
topic_model = BERTopic(embedding_model="xlm-r-bert-base-nli-stsb-mean-tokens")

Or select a SentenceTransformer model with your own parameters:


In [ ]:
from sentence_transformers import SentenceTransformer

sentence_model = SentenceTransformer("distilbert-base-nli-mean-tokens", device="cpu")
topic_model = BERTopic(embedding_model=sentence_model, verbose=True)

Click [here](https://www.sbert.net/docs/pretrained_models.html) for a list of supported sentence transformers models.  
